In [1]:
import pandas as pd
import re
import string
import time

from collections import Counter, defaultdict

from needleman_wunsch import needleman_wunsch

from fuzzywuzzy import fuzz

from operator import itemgetter

pd.set_option('display.max_rows', 1000)

In [2]:
df = pd.read_csv('data/dataYiddish/ybc/all-titles-ybc.csv')

In [3]:
df.sample()

title        author             title-trans  \
10295  אמאל איז געווען א מענטש  טאפעל, יהודה  Amol iz geṿen a menṭsh   

                  author-trans  
10295  Tofel, Yehudah, b. 1891

In [4]:
len(df)

11707

In [5]:
title_df = df[['title', 'title-trans']]
author_df = df[['author', 'author-trans']]

title_df.columns  =  ['yiddish', 'translit']
author_df.columns  =  ['yiddish', 'translit']

df_ = pd.concat([title_df, author_df]).reset_index(drop=True)

In [6]:
len(df_)

23414

In [7]:
df_

yiddish  \
0      ארץ-ישראל : איינדריקן און בילדער   
1       א פרעמדע וועלט : ראמאן, בוך פיר   
2                         ערעוו : ראמאן   
3          באלאדעס פון מיין חרובער היים   
4       טירן און פענצטער : דערציילונגען   
...                                 ...   
23409         פרידמאן, בצלאל, 1897-1941   
23410                  שטשאװינסקי, יוסף   
23411                         ספר, ש. א   
23412                          שבת, שרה   
23413            פידעדער-מארגאליס, חיים   

                                                translit  
0                        Erts-Yiśroel ayndriḳn un bilder  
1      A fremde ṿelṭ roman, bukh fir ; In nayem land,...  
2                                             Ereṿ roman  
3                          Balades fun mayn ḥorever heym  
4                         Ṭirn un fentsṭer dertseylungen  
...                                                  ...  
23409                       Friedman, Bezalel, 1897-1941  
23410                                  Shavinsky, Joseph  
23411                                       Sofer, Sh. A  
23412                                      Shabath, Sara  
23413                            Fiderer-Margolis, Chiam  

[23414 rows x 2 columns]

In [8]:
df_ = df_[(df_.yiddish.notna() & df_.translit.notna())]
len(df_)

21092

In [9]:
apo = '&#039;'

df_['yiddish_'] = df_.yiddish.apply(lambda x: re.sub(apo, '\'', x))
df_['translit_'] = df_.translit.apply(lambda x: re.sub(apo, '\'', x))

/home/iz/miniconda3/envs/kohan/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/iz/miniconda3/envs/kohan/lib/python3.7/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [ ]:
#df_['yiddish_'] = df_.yiddish.apply(lambda x: re.sub('[^\u0590-\u05fe \-]+', '', x))
#df_['translit_'] = df_.translit.apply(lambda x: re.sub('[^\w \-]+', '', x))

In [ ]:
#df_['yiddish_'] = df_.yiddish.apply(lambda x: re.sub('\d+ ?\-\d*', '', x))
#df_['translit_'] = df_.translit.apply(lambda x: re.sub('\d+ ?\-\d*', '', x))

In [10]:
df_.sample()

yiddish                translit yiddish_               translit_
21540  קאץ, פ  Ḳats, Pinye, 1882-1959   קאץ, פ  Ḳats, Pinye, 1882-1959

In [11]:
letterpairs = [(pair[0][0], pair[1][0].lower()) for pair in zip(df_.yiddish_.values, df_.translit_.values)]

In [17]:
letterdict = defaultdict(str)

for tup in Counter(letterpairs).most_common()[::-1]:
    letterdict[tup[0][0]] = tup[0][1]

In [18]:
letterdict[' '] = ' '
letterdict['ן'] = 'n'
letterdict['ם'] = 'm'
letterdict['ץ'] = 'ts'
letterdict['ף'] = 'f'
letterdict['ך'] = 'kh'
letterdict['צ'] = 'ts'
letterdict['ט'] = 'ṭ'

In [16]:
letterdict

defaultdict(str,
            {'ה': 'h',
             'ב': 'b',
             'פ': 'f',
             'א': 'a',
             'ז': 'z',
             'מ': 'm',
             'ו': 'ṿ',
             'װ': 'w',
             'צ': 't',
             'ר': 'r',
             'ש': 's',
             'ג': 'g',
             'ק': 'k',
             'ט': 't',
             'ח': 'ḥ',
             '\u200f': 'g',
             'ל': 'l',
             'י': 'y',
             'ד': 'd',
             'ס': 's',
             'נ': 'n',
             '@': 'a',
             'ע': 'e',
             '%': '1',
             'A': 'a',
             ':': 'm',
             '.': 'h',
             '9': '9',
             '?': 'i',
             '(': 'a',
             '_': 'i',
             ' ': ' ',
             'כ': 'k',
             '8': 'i',
             'I': 'i',
             'W': 'w',
             '&': '&',
             '2': '2',
             'T': 't',
             'Y': 'y',
             'ת': 't',
             'ײ': 'y',
            

In [19]:
wordlist = []
worddict = {'אין': 'in', 'און': 'un'}

for heb, lat in zip(df_.yiddish_.values, df_.translit_.values):
    matches = defaultdict(lambda: ('', 0),)
    for i, word in enumerate(heb.split()):
        if word in worddict.keys():
            pseudotrans = worddict[word]
        else:
            pseudotrans = ''.join([letterdict[letter] for letter in word]) 
        ratios = []
        for j, trans in enumerate(lat.split()):
            ratio = fuzz.ratio(pseudotrans.lower(), trans.lower()) - abs(i-j)
            ratios.append((trans, pseudotrans, ratio))
        maxratio = max(ratios, key=itemgetter(2))
        print(maxratio)
        if maxratio[2] >= 50:
            if matches[maxratio[0]][1] >= maxratio[2]:
                pass
            elif matches[maxratio[0]][1] < maxratio[2]:
                matches[maxratio[0]] = (word, maxratio[2])
    for key, val in matches.items():
        wordlist.append((val[0], key))
        print(val[0], key)
    print()

('Erts-Yiśroel', 'artsysral', 57)
('ayndriḳn', 'm', 0)
('ayndriḳn', 'ayyndrykn', 70)
('un', 'un', 99)
('bilder', 'bylder', 82)
ארץ-ישראל Erts-Yiśroel
איינדריקן ayndriḳn
און un
בילדער bilder

('A', 'a', 100)
('fremde', 'fremde', 100)
('ṿelṭ', 'ṿṿelṭ', 89)
('roman,', 'm', 29)
('roman', 'raman', 74)
('bukh', 'bṿkh', 74)
('fir', 'fyr', 66)
א A
פרעמדע fremde
וועלט ṿelṭ
ראמאן, roman
בוך bukh
פיר fir

('Ereṿ', 'ereṿṿ', 89)
('roman', 'm', 33)
('roman', 'raman', 79)
ערעוו Ereṿ
ראמאן roman

('Balades', 'balades', 100)
('fun', 'fṿn', 67)
('mayn', 'myyn', 75)
('ḥorever', 'ḥrṿber', 62)
('heym', 'hyym', 75)
באלאדעס Balades
פון fun
מיין mayn
חרובער ḥorever
היים heym

('Ṭirn', 'ṭyrn', 75)
('un', 'un', 100)
('fentsṭer', 'fentsṭer', 100)
('dertseylungen', 'm', 0)
('dertseylungen', 'dertsyylṿngen', 84)
טירן Ṭirn
און un
פענצטער fentsṭer
דערציילונגען dertseylungen

('Un', 'un', 100)
('in', 'in', 100)
('dayn', 'dyyn', 75)
('bluṭ', 'blṿṭ', 75)
('zolsṭu', 'zalsṭṿ', 67)
('lebn', 'lebn', 100)
('(ṭog-bukh', 'm',

('in', 'in', 100)
('fir', '4', 0)
('aḳṭn', 'akṭn', 75)
דער Der
קאטער ḳoṭer
אין in
שטיוול shṭiṿl
א a
קינדער-פיעסע pyese
מיט miṭ
געזאנג gezang
און un
טענץ ṭents
אקטן aḳṭn

('In', 'in', 100)
('mayn', 'myyn', 75)
('glezernem', 'glezernem', 100)
('ṭurem', 'ṭṿrem', 80)
('mayn', 'm', 37)
('moshl', 'msl', 74)
('un', 'un', 99)
('saṭire', 'saṭyre', 82)
אין In
מיין mayn
גלעזערנעם glezernem
טורעם ṭurem
משל moshl
און un
סאטירע saṭire

('Dos', 'das', 67)
('ḳelbl', 'kelbl', 80)
דאס Dos
קעלבל ḳelbl

('Geklibene', 'geklybene', 89)
('shrifṭen', 'sryfṭen', 80)
געקליבענע Geklibene
שריפטען shrifṭen

('Eden', 'edn', 86)
('ha-yeladim', 'hyldym', 62)
('im', 'm', 62)
('sefer', 'sfr', 74)
('miḳra', 'mkra', 66)
('li-yeladim', 'lyldym', 61)
('ṿeli-yeladot', 'ṿlyldṿt', 62)
('im', 'm', 67)
('im', 'em', 49)
('tirgum', 'trgṿm', 72)
('ha-milim', 'hmlym', 61)
('be-arba', 'barbe', 66)
('leshonot', 'lsṿnṿt', 56)
('im', 'm', 61)
('Rusit,', 'rṿsyt', 54)
('Ashkenazit,', 'asknzyt', 66)
('Tsarfatit', 'tsrftyt', 74)
('ṿe-Angli

('tsayṭ', 'tsyyṭ', 79)
קאלאניע Ḳolonye
לוסיענוויל Lusienṿil
צו tsu
דער der
געשיכטע geshikhṭe
פון fun
אנטשטייאונג anṭshṭeyung
און un
אנטוויקלונג anṭṿiḳlung
קאלאניע, ḳolonye,
אין in
פראווינץ proṿints
ענטרע Enṭre
במשך bemeshekh
37 37
יאר yor
צייט tsayṭ

('Dos', 'das', 67)
('vunder', 'ṿṿṿnder', 62)
('fun', 'fṿn', 67)
('Mizreḥ-Eyropeyishe', 'mzrḥayyrafeysn', 56)
('yidnṭum', 'yydnṭṿm', 71)
דאס Dos
ווונדער vunder
פון fun
מזרח-אייראפעישן Mizreḥ-Eyropeyishe
יידנטום yidnṭum

('A', 'a', 100)
('boym', 'bṿym', 75)
('in', 'in', 100)
('ṿinṭ', 'ṿṿynṭ', 67)
('boym', 'm', 37)
('dertseylungen', 'dertsyylṿngen', 84)
א A
בוים boym
אין in
ווינט ṿinṭ
דערציילונגען dertseylungen

('Un', 'un', 100)
('di', 'dy', 50)
('zun', 'zṿn', 67)
('hoṭ', 'haṭ', 67)
('geshaynṭ', 'gesyynṭ', 80)
און Un
די di
זון zun
האט hoṭ
געשיינט geshaynṭ

('Zumer-leben', 'zṿmerleben', 86)
זומער-לעבען Zumer-leben

('[Tanakh]', '[tn&kh', 71)
('neviim,', 'm', 24)
('Toyre,', 'trh', 43)
('neviim,', 'nbyaym', 30)
('Toyre,', 'ktbym', 33)
[תנ&quot;

('elṭsṭe', 'elṭsṭe', 98)
('tsayṭn', 'tsyyṭn', 81)
('biz', 'byz', 65)
('tsu', 'tsṿ', 65)
('haynṭiḳer', 'hyynṭyker', 66)
('tsayṭ', 'tsyyṭ', 79)
('tsayṭ', 'm', -2)
('di', 'in', 40)
('tsayṭn', 'tsen', 51)
('der', 'bend', 22)
וועלט-געשיכטע Ṿelṭ-geshikhṭe
פון fun
יידישן Yidishn
עלטסטע elṭsṭe
צייטן tsayṭn
ביז biz
צו tsu
היינטיקער haynṭiḳer
צייט tsayṭ

('Gezamelṭe', 'gezamelṭe', 100)
('dramen', 'dramen', 100)
געזאמעלטע Gezamelṭe
דראמען dramen

('Ale', 'ale', 100)
('ṿerḳ', 'ṿṿerk', 67)
('fun', 'fṿn', 67)
('Avraham', 'abrhm', 67)
('Reyzen', 'ryyzen', 83)
('Avraham', 'm', 23)
('in', 'in', 99)
('12', '12', 99)
('bender', 'bender', 99)
אלע Ale
ווערק ṿerḳ
פון fun
אברהם Avraham
רייזען Reyzen
אין in
12 12
בענדער bender

('Fun', 'fṿn', 67)
('unzer', 'aṿner', 60)
('alṭen', 'alṭen', 100)
('oytser', 'aṿtsr', 55)
('geḳlibene', 'm', 0)
('geḳlibene', 'geklybene', 77)
('perl', 'ferl', 74)
('fun', 'fṿn', 66)
('unzere', 'aṿmzere', 61)
('alṭe', 'alṭe', 99)
('ḳṿolen', 'kṿṿalen', 61)
('ayngeṭaylṭ', 'hhh', 0)
('ayn


('Esterḳe', 'astrke', 62)
('ertsehlung', 'm', 0)
('ertsehlung', 'ertsehlṿng', 89)
אסתרקע Esterḳe
ערצעהלונג ertsehlung

('A', 'a', 100)
('likhṭiḳe', 'lykṭyke', 53)
('ṿelṭ', 'ṿṿelṭ', 89)
('mayśes̀', 'm', 24)
('ḳinder', 'kynder', 66)
('mayśes̀', 'myyses', 61)
א A
ליכטיקע likhṭiḳe
וועלט ṿelṭ
קינדער ḳinder
מייסעס mayśes̀

('Yanḳev', 'yekb', 40)
('Gordin', 'gardyn', 67)
גארדין Gordin

('Ḳinder-hertser', 'kynderhertser', 81)
קינדער-הערצער Ḳinder-hertser

('Amoliḳe', 'amalyke', 57)
('doyres̀', 'dṿrṿt', 33)
אמאליקע Amoliḳe

('Dos', 'das', 67)
('hoyz', 'hz', 67)
('fun', 'fṿn', 67)
('di', 'dy', 50)
('lalkes', 'lalkes', 100)
דאס Dos
הױז hoyz
פון fun
די di
לאלקעס lalkes

('Lidelekh', 'lydelekh', 88)
('mayne', 'myyne', 80)
('mayne', 'nḥṿm', 21)
('mayne', 'ṿṿyysman', 44)
לידעלעך Lidelekh
מיינע mayne

('Sharey', 'saryy', 73)
('lider', 'm', 0)
('lider', 'lyder', 79)
שאריי Sharey
לידער lider

('Mayne', 'myyne', 80)
('zikhroynes̀', 'zykrṿnṿt', 42)
מיינע Mayne

('Milon', 'mlṿn', 67)
('ḥadish', 'ḥdys', 60

...

('Reuben,', 'raṿbn', 50)
ראובן Reuben,

('Tsanin,', 'tsanyn', 77)
('M,', 'm', 67)
('1906-', '196', 75)
צאנין, Tsanin,
מ, M,
1906- 1906-

('Lederman,', 'lederman', 94)
('Lederman,', 'mshbynem', 23)
לעדערמאן, Lederman,

('Landau,', 'landṿy', 62)
('Zisha,', 'zysa', 60)
('1889-1937', '1ii91937', 71)
לאנדוי, Landau,
זישא, Zisha,
1889-1937 1889-1937

('Menaḥem', 'mnḥm', 73)
('Mendl', 'mndl', 89)
מנחם Menaḥem
מנדל Mendl

('Elkin,', 'elkyn', 73)
('Mendl,', 'mendel', 83)
עלקין, Elkin,
מענדעל Mendl,

('Mendele', 'mendele', 100)
('Sefarim,', 'mṿykersfarym', 49)
מענדעלע Mendele

('Elkin,', 'elkyn', 73)
('Mendl,', 'mendl', 91)
עלקין, Elkin,
מענדל Mendl,

('Vinokur,', 'ṿṿyynrṿykh', 22)
('Grigory,', 'hersl', 15)

('Noṿiḳ,', 'nawyk', 18)
('P,', 'f', 0)

('Manouilskii,', 'manṿylsky', 57)
('Dmitri', 'd', 29)
מאנוילסקי, Manouilskii,

('Malach,', 'mlakh', 67)
('Leib,', 'l', 33)
מלאך, Malach,

('Dostoyevsky,', 'dṿsṭṿybsky', 55)
('Fyodor,', 'fy', 44)
('1821-1881', '1i211ii1', 59)
דוסטויבסקי, Dostoyevsky,
18

('1849-1912', '1i491912', 82)
סטרינדבערג, Strindberg,
אגוסט, August,
1849-1912 1849-1912

('Lerner,', 'lerner', 92)
('Falik', 'falyk', 80)
לערנער, Lerner,
פאליק Falik

('Averchenko,', 'aṿṿerṭsenka', 55)
('Arkadii,', 'arkady', 71)
אווערטשענקא, Averchenko,
ארקאדי Arkadii,

('Suttner,', 'zṿṭner', 43)
('Bertha', 'berṭha', 83)
בערטהא Bertha

('Weitz,', 'ṿṿyyts', 17)
('A', 'abrhm', 33)

('Hamsun,', 'hamsṿn', 77)
('Knut,', 'knṿṭ', 44)
('1859-1952', '1i591952', 82)
האמסון, Hamsun,
1859-1952 1859-1952

('Kazdan,', 'kazdan', 92)
('Ḥayyim', 'ḥh', 25)
('Solomon,', 's', 22)
קאזדאן, Kazdan,

('Podriachik,', 'fadryaṭsyk', 38)
('Eliezer,', 'alyezr', 57)
('1914-', '1914', 89)
אליעזר, Eliezer,
1914- 1914-

('Lurye,', 'lṿrye', 73)
('Noṭe,', 'naṭe', 67)
('1906-', '196', 75)
לוריע, Lurye,
נאטע, Noṭe,
1906- 1906-

('Rappaport,', 'rafafarṭ', 44)
('Aaron,', 'ahrn', 60)
אהרן Aaron,

('Sholem', 'slṿm', 60)
('Sholem', 'elykm', 35)
('1859-1916', '1i591916', 82)
שלום Sholem
1859-1916 1859-1916

('Eisland,', 'ayyzl

‏גלאטשטיין, Glatstein,
‏1896-1971 1896-1971

('Weprinsky,', 'ṿṿefrynsky', 60)
('Roshelle', 'rasel', 62)
וועפרינסקי, Weprinsky,
ראשעל Roshelle

('Singer,', 'zynger', 62)
('Jacob,', 'yekb', 20)
זינגער, Singer,

('Vilʹsker,', 'wylsker', 62)
('Leĭb', 'lyb', 57)
װילסקער, Vilʹsker,
לײב Leĭb

('Leṿin,', 'lewyn', 55)
('L', 'l', 100)
לעװין, Leṿin,
ל L

('Golbshṭeyn,', 'galbsṭyyn', 70)
('M', 'm', 100)
גאלבשטיינ, Golbshṭeyn,
מ M

('Sfard,', 'sfard', 91)
('David', 'dṿd', 50)
ספארד, Sfard,
דוד David

('Rozoṿsḳi,', 'razawsky', 35)
('Mordekhai,', 'mrdky', 53)
מרדכי Mordekhai,

('Opatoshu,', 'afaṭasṿ', 25)
('Joseph,', 'yṿsf', 18)

('Steinbaum,', 'sṭyynbṿym', 42)
('Israel', 'y', 0)

('Malamuṭ,', 'malamṿṭ', 80)
('Y.', 'yṿsf', 33)
('L,', 'lyb', 40)
('1886-', '1ii6', 44)
מאלאמוט, Malamuṭ,

('Medem,', 'medem', 91)
('Gina', 'gyna', 75)
מעדעם, Medem,
גינא Gina

('Pomerantz,', 'famerants', 63)
('Alexander,', 'a', 18)
פאמעראנץ, Pomerantz,

('Ghitzis,', 'gytsys', 43)
('M,', 'm', 67)
מ M,

('Maupassant,', 'mafas


('Hurṿits-Zalḳes,', 'hṿrṿṿyts', 43)
('Sh,', 's', 50)
ש Sh,

('Trunk,', 'ṭrṿnk', 55)
('Yeshaia,', 'yh', 39)
('Yeḥiel', 'y', 28)
טרונק, Trunk,

('Hofstein,', 'hafsṭyyn', 47)
('David,', 'daṿṿyd', 50)
דאוויד David,

('Wygodzki,', 'wygadzky', 71)
('Stanisław,', 's', 18)
װיגאדזקי, Wygodzki,

('Ṭayṭsh,', 'ṭyṭs', 73)
('Yaḳov', 'y', 33)
טײטש, Ṭayṭsh,

('Schulstein,', 'sṿlsṭyyn', 42)
('Moses', 'msh', 50)
משה Moses

('Tsanin,', 'tsanyn', 77)
('M,', 'mrdky', 29)
('1906-2009', '196', 50)
צאנין, Tsanin,
1906- 1906-2009

('Zeṿin,', 'zeṿṿyn', 67)
('Y.', 'y', 67)
זעווין, Zeṿin,
י Y.

('Rechtman,', 'rekṭmn', 53)
('Abraham', 'abrhm', 83)
רעכטמן, Rechtman,
אברהם Abraham

('Hirschbein,', 'hyrsbyn', 56)
('Peretz,', 'frts', 36)
הירשבײן, Hirschbein,

('Asch,', 'as', 57)
('Sholem,', 'slṿm', 55)
אש, Asch,
שלום Sholem,

('Graetz,', 'greṭts', 62)
('Graetz,', 'tsby', 17)
גרעטץ, Graetz,

('Reisen,', 'ryyzen', 46)
('Abraham,', 'abrhm', 77)
אברהם Abraham,

('Sholem', 'slṿm', 60)
('Sholem', 'elykm', 35)
שלום Sholem



סינקלער, Sinclair,

('Unterman,', 'aṿnṭerman', 67)
('Isaac,', 'ytsḥk', 18)
אונטערמאן, Unterman,

('Zineman,', 'tsyneman', 62)
('Jakub', 'yekb', 44)
צינעמאן, Zineman,

('Lastik,', 'lasṭyk', 62)
('Salomon', 'slmh', 55)
לאסטיק, Lastik,
שלמה Salomon

('Wassermann,', 'waserman', 84)
('Jakob,', 'yekb', 40)
('1873-1934', '1i731934', 82)
װאסערמאן, Wassermann,
1873-1934 1873-1934

('Chekhov,', 'ṭsekaw', 29)
('Pavlovich,', 'ahf', 30)

('Noṿiḳ,', 'naṿṿyk', 33)
('P,', 'f', 0)
('1891-', '1i91', 67)
1891- 1891-

('Piloṿsḳi,', 'fylaṿṿsky', 33)
('Yaaḳov,', 'yekb', 18)

('Lewin,', 'leṿṿyn', 50)
('Isaac,', 'ytsḥk', 18)
לעווין, Lewin,

('Mishḳin,', 'frns', 17)
('Mishḳin,', 'm', 21)

('Goldenstein,', 'galdensṭyyn', 61)
('Haim,', 'ḥyym', 22)
גאלדענשטיין, Goldenstein,

('Langfus,', 'langfṿs', 80)
('Anna,', 'anna', 89)
לאנגפוס, Langfus,
אננא Anna,

('Lurye,', 'lṿrye', 73)
('Noṭe,', 'naṭe', 67)
לוריע, Lurye,
נאטע Noṭe,

('Korn,', 'karn', 67)
('Rachel', 'rḥl', 44)
('H,', 'h', 67)
קארן, Korn,
ה H,

('Corona,', 

In [21]:
pair_df = pd.DataFrame({'yiddish': [tup[0] for tup in wordlist], 'translit': [tup[1] for tup in wordlist]})

In [22]:
pair_df['source'] = 'ybc'

In [23]:
len(pair_df), len(pair_df.drop_duplicates())

(67989, 18011)

In [24]:
pair_df.drop_duplicates().to_csv('data/processed-parallel/ybc.csv', index=False)